In [1]:
from transformers import AutoModelForCausalLM, AutoTokenizer, pipeline

/home/ubuntu/.local/lib/python3.9/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [22]:
generator = pipeline('text-generation', model='./huggingface/kogpt-neox-tiny', device='cuda:0')

In [26]:
def generate(prefix: str):
    print(generator(prefix, do_sample=True, top_p=0.6, repetition_penalty=1.4, max_length=128, penalty_alpha=0.6)[0]["generated_text"])

generate("0 : 만약 오늘이 ")
generate("오늘 정부가 발표한 내용에 따르면")
generate("수학이란 학자들의 정의에 따라")
generate("영상 보는데 너무 웃겨 ")

0 : 만약 오늘이 #@이름#가 먼저 자는거면 또 자는건데ㅋ
1 : ㅇㄷㆍ_==
2 : 아까 아침에 일어났어?!!
3 : 아니아니 근데 이따 시간표가 끝날때까지 잤지않게 일주일동안 계속 잠들었엉.. 나도 지금 일어났는데, 너무 늦을듯해. 그러다 다시 일어나서 다행이다
4 : 어차피 2:30분에 출발할것같아요~
5 : 이제 곧 일어낫어요
오늘 정부가 발표한 내용에 따르면, 한참 여부는 "한숨이 살릴 수 있는 게 무엇인가"라는 질문에 대해 말할 것도 없다. 하지만 그건 바로 이러한 문제 때문일 것이다."
실제로 해당 기사에서 나온 바 있다. 실제로 당시 한국에서 이게 사실이 아니라고 밝혔다는 건데도 불구하고 말이다. 기사화되기는 했는데 '한국어'의 경우에도 논란이 있었다. 사실 이 부분만 언급되어있고, 대한민국은 무조건 비난을 하는 것이 아니라 본인의 실수를 저지른다는 것인데 반해 유튜브 채널의 영상에서는 그냥 저런 댓글이 올라오
수학이란 학자들의 정의에 따라 이 교과서에서 교육하는 경우가 많은데, 그 이유는 교수들(실제로 학생들은 공부도 하교할 수 있는 등)을 학교로 삼아 강의실에서 듣기 때문이다.
이 학교의 교사들이 '학교'를 선택한 것은 아니지만 교사가 "학생들의"라는 뜻이다."라고 한다. 하지만 이쪽은 교사와 함께 한 명씩 입학식 전부터 교사의 인생들을 시험해보고 싶다는 의미다. 또한 수학여행에서는 가르칠 수도 있고 수학여행을 갔거나 전공 과목으로 졸업하고 교사는 다른
영상 보는데 너무 웃겨 #@기타#웃기네
0 : ㅋㅌㄱㆍ이별명인듯
1 : ㅠㅜ그렇지뭐? 아빠는 아니고? 왜케 많음... 나도 그럴수가 없어.. 내가 말한건데 ㅎ,, #@이름#씨에스나게놀아주까봐 어제부터 내맘대로해달라햇어 그래서 우리집에서 안쓰럽거든 근데 진짜 많이해서 걱정하지말라고 해줬으면좋


In [45]:
from torch.utils.data import Dataset
import jsonlines
from dataclasses import dataclass
import os
import random


@dataclass
class InfiniteFileIterator:
    file: str

    def __iter__(self):
        
        while True:
            with jsonlines.open(self.file) as f:
                for item in f:
                    yield item


class PLMDataset(Dataset):

    def __init__(self, dir_path: str) -> None:
        super().__init__()
        self.files = [os.path.join(dir_path, p) for p in os.listdir(dir_path)]
        
        weights = [os.path.getsize(f) for f in self.files]
        wsum = sum(weights)
        
        # 파일 크기로 가중치를 줍니다
        self.weights = [w / wsum for w in weights]

    def __iter__(self):
        iters = [iter(InfiniteFileIterator(f)) for f in self.files]

        while True:
            item_iter = random.choices(iters, self.weights, k=1)[0]
            item = next(item_iter)
            yield item

In [46]:
dataset = PLMDataset("data/test/")
dataset_iter = iter(dataset)

In [47]:
print(dataset.files, dataset.weights)

['data/test/heegyu__nikl_messenger_dialog_gpt.jsonl', 'data/test/heegyu__kowikitext.json', 'data/test/heegyu__nikl_spoken.jsonl', 'data/test/heegyu__nia_web.jsonl', 'data/test/heegyu__aihub_sns_dialog_gpt.jsonl', 'data/test/heegyu__nikl_written.jsonl', 'data/test/heegyu__nikl_daily_dialog_v1.2.jsonl', 'data/test/heegyu__namuwiki-extracted.json', 'data/test/heegyu__korean-petitions.jsonl', 'data/test/heegyu__aihub_spoken_2021.jsonl'] [0.0008229597362719931, 0.03303081164439255, 0.04629194599488135, 0.46909979918133277, 0.029735150689437537, 0.1275363883317153, 0.001095550010914665, 0.25112683730890817, 0.02269146556901579, 0.018569091533129838]


In [43]:
for i, item in enumerate(dataset_iter):
    print(item)
    if i == 100:
        break

{'text': '01범보다 무서운 곶감\n화자를 처음 만나 이야기를 들으러 왔다고 하자 서슴없이 꺼낸 첫 이야기이다. 화자로서 가장 쉽게 기억해낸 이야기인 셈이다. 설화 앞뒤에 교훈적 해석을 덧붙이고 있음은 화자의 습관화된 태도의 한 모습이기도 하다. 어려서 조모로부터 들었다고 했다.\n그링깨. 사람이 어거지루는 못 살구. 응? 어거지루 안 되능 거여. 사람이 그링깨 뭐이냐 하먼 자연~간 제절루 되야지 어거지루는 못 살어, 사람이.\n그래 옛날, 그 꼭감이라능 게 말여. 사람이 먹잖야 이케? 먹지마는. 그게 참 무성(무서운) 거여.\n애기가 울어. 옛날에. 그래 할머니가 달갸(달래). 그때 호랭이가, 응? 그 집 문앜이 와 섰어 지금. 옛날이는 호랭이가 말두 하구 그랴. 그래 인제 그 할머니가 애기를 달램성 왼갖 소리를 다 햐. ‘호랭이 왔다’구 해두 울구우, ‘괭이 왔다’두 울구, 왼갖 소리를 다 해두 울어.\n그랑깨 꼭감을,\n“아나, 꼭감.”\n“아가, 꼭감.”\n그랑깨 꺄. 안 울어.\n호랭이 생각이? ‘야아, 이거 내가 젤 무선 짐승인디 말여? 나보다 무서웅 게 익구나. 호랭이, 꼭감이, 꼭갬이 참 무석구나.’ 싶어서, 인제…\n근디 인제, 그 집이 말여. 왱깐이(외양간에) 가 숨었어. 인제. 무서서.\n소도둑놈이 소를 몰러 와서 봉깨, 함 마리가 익거덩? 가서 인제 소 손지 알구 말여. 꼬랭이를 집어탔어.\n그러닝깨 이 호랭이는 꼭갬인지 알구 말여. 그 사람을. ‘아따! 꼭갬이로구나’ 싶어서 인제 그 눔을 실쿠 사알살 가 지금. 그래 도독놈은 인제 호랭인 줄 몰르구 말여, 손주(소인 줄) 알구 말여, 이 눔을 인제 갈기를 거머쥐구 집어타구서는 사알살 가는디. 아 이 뉨이 산 속으루 들어간다 인제? 그래 산 속으루 들어강깨 날이 샜어 인제.\n그라자 곰이 말여? 곰을 만내서 곰이 하는 말이,\n“아 호새원(호생원)?”\n“왜 그라냐?”\n“아 왜 밥얼 실쿠 와요?”\n“예끼 놈! 이게 꼭감이다. 큰일 난다. 저리 가거라.”\n“아니 밥여요. 밥여. 

In [44]:
iters = [iter(InfiniteFileIterator(f)) for f in dataset.files]

for i in range(100):
    item_iter = random.choices(iters, dataset.weights, k=1)[0]
    item = next(item_iter)
    print(item)

{'text': '저는 여행 다니는 것을 굉장히 좋아하는데요. 그래가지고 스페인이나 뭐 영국 유럽 아니면 국내에서도 뭐 강릉이나 전주 같은 데를 많이 다녔는데 혹시 여행 다니는 거 좋아하시나요?\n저 여행 다니는 거 되게 좋아해서 대학교 내내 여행을 엄청 많이 다녔었는데요. 제가 고등학교 때는 여행에 대해 흥미가 없었는데 그게 좀 아버지가 짠대로 패키지처럼 여행을 다녀서 그런 것 같아요. 그래서 대학교 간 이후로는 해외여행을 되게 많이 갔었는데 그중에서 제일 기 좋았던 거는 스페인이랑 포르투갈이었거든요. 어~ 혹시 포르투갈이나 스페인 유럽 쪽 다녀오신 적 있으신가요?\n어~ 네. 저도 우연히 스페인과 포르투갈을 다녀왔었었습니다. 어~ 저는 스페인 중에서도 마드리드에 근교에 있었던 톨레도라는 지역이 굉장히 좋았는데요. 그 톨레도에서 특히 기억에 남았던 거는 거기에 대성당이 있는데 그 성당이 엄청 화려하더라고요. 그래서 거기를 꾸며논 거를 보면은 금을 엄청 많이 사용해가지고 되게 빤짝빤짝하고 좀 성당은 보통 좀 소박하다라는 인식이 있었는데 아~ 이렇게 화려한 성당도 있구나라는 거를 새롭게 알게 됐었습니다. 어~ 또 톨레도에 지역 음식도 같이 먹었었는데 아~ 이름은 지금 잘 생각이 나지는 않지만 굉장히 달달했던 그런 디저트 종류였는데 그~ 디저트도 먹고 그다음에 천천히 걸어 다니면서 주변 풍경도 보고 근교 여행만의 약간 소박한 맛이 있었다고 생각을 합니다. 어~ 또 물론 마드리드도 굉장히 좋았는데 유럽 여행을 많이 가셨다고 해서 혹시 톨레도도 가본 적이 있나요?\n아~ 제가 톨레도도 다녀왔는데 저는 이제 여행 일정을 길게 잡아서 톨레도는 하루를 봤는데 도 그렇게 너무 더웠기 때문에 많이 보진 못한 것 같아요. 그때는 버스 관광버스를 타고 계속 돌아다니면서 이제 내리는 데마다 관광을 할 수 있는 버스를 탔는데요. 그 버스를 타고 전체를 다 내려서 보려고 했지만 날씨가 너무 더워서 금방 금방 이제 xx 장소로 넘어갔던 것 같 같습니다. 거기는 이제 고대 도시라고 해서 